In [ ]:
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

import time

# Étudiants et étudiantes dans le groupe

- ...
- ...
- ...

# Instructions TP noté

Le TP doit être réalisé par groupe de 2 ou 3 personnes. Il faut indiquer les noms ci-dessus.
Chaque groupe doit rendre à 12h30 au plus tard :

- un rapport manuscrit qui doit être rendu en main propre à 12h30
- le code du TP complété par email à caio.corro@limsi.fr (inclure le nom des étudiants dans le message) =>  envoie à 12h30 au plus tard, 12h35 c'est déjà trop tard.

**Soumission du code:** uniquement un fichier .ipynb (pas de .html, pas de .py, etc), éventuellement zipé, ne pas m'envoyer les données.

**Attention:** Le code sera testé automatiquement, il faut donc bien faire attention aux entrées/sorties attendues, le retour attendu, les dimensions, etc.

**Instructions pour le rapport manuscrit:**
Le rapport doit contenir les choses suivantes :

- présentation des modèles, dérivation des équations (et autres formules), etc ;
- explication des implémentations, à quoi faire attention, etc ;
- des résultats expérimentaux et commentaires sur ceux ci (qu'est ce qu'on observe au niveau de la qualité des prédictions ? vitesse d'entrainement, etc).

Ce rapport doit avoir la forme d'un tutoriel. Imaginez que vous essayez de m'apprendre ce qu'est la régression linéaire et comment on implémente un tel modèle.

Quelques points important :

- il faut être formelle ! Mais vous pouvez utiliser des schéma en plus pour guider vos explications ;
- tout doit être dans le rapport manuscrit, et non dans le notebook --- le notebook ne contenir que le code, avec éventuellement des commentaires pour aider la lecture du code ou faire des références au rapport.

# TP 4 : régression linéaire

L'objectif de ce TP est d'implémenter plusieurs algorithmes pour l'apprentissage d'un modèle de linéaire et de les comparer entre eux.
Nous utiliserons pour cela des données en "grande" dimension (une entrée contient 384 features).
Le problème étuidé est un problème de régression.


Commencez par télécharger les données ici : https://archive.ics.uci.edu/ml/datasets/Relative+location+of+CT+slices+on+axial+axis

In [ ]:
#https://archive.ics.uci.edu/ml/datasets/Relative+location+of+CT+slices+on+axial+axis

def read_data(path):
    raw_data = list()
    with open(path) as instream:
        next(instream)
        for line in instream:
            line = line.strip()
            if len(line) == 0:
                continue
            vs = [float(v) for v in line.split(",")[1:]]
            raw_data.append(vs)
            
    X = np.empty((len(raw_data), len(raw_data[0]) - 1))
    y = np.empty(len(raw_data))
    for i, r in enumerate(raw_data):
        X[i] = r[:-1]
        y[i] = r[-1]
    return X, y

X_all, y_all = read_data("slice_localization_data.csv")
X_all.shape, y_all.shape

train_mask = np.arange(X_all.shape[0]) % 5 != 0

X_train = X_all[train_mask]
y_train = y_all[train_mask]

X_test = X_all[np.logical_not(train_mask)]
y_test = y_all[np.logical_not(train_mask)]

# Données d'entrainement
print(X_train.shape, y_train.shape)
# Données de test
print(X_test.shape, y_test.shape)

## Descente de gradient et régularization L2

Dans un premier temps, nous implémenterons une descente de gradient avec ou sans régularisation L2.
La fonction de perte à utiliser est l'erreur quadratique moyenne.

On commence par implémenter deux fonctions qui seront utiles pour la suite.

In [ ]:
# Retourne la prédiction pour toutes les données en entrée
# arguments:
# - a, b: paramêtres du modèle
# - X: entrées, chaque ligne correspond à une entrée et chaque colonnne à une feature
# retourne:
# - les prédictions du modèle sous forme d'un vecteur
def predict(a, b, X):
    # TODO
    # ...

# Retourne l'erreur quadratique moyenne entre des valeurs de référence et des prédictions
# (même chose que la fonction de perte !)
# arguments:
# - y_gold: vecteur, valeurs de référence
# - y_pred: vecteur, valeurs prédites par le modèle
def mean_square_error(y_gold, y_pred):
    # TODO
    # ...

In [ ]:
# pour tester

a = np.random.rand(X_train.shape[1])
b = np.random.rand(1)

assert predict(a, b, X_test).shape == y_test.shape

mean_square_error(y_test, predict(a, b, X_test))

La fonction suivante doit faire une étape de descente de gradient.

- les modifications des paramètres doivent se faire "in place"
- il faut retourner la valeur de la loss (un scalaire)

**Conseil:** dans un premier temps, vous pouvez implémenter et tester sans la régularisation

In [ ]:
# arguments:
# - a, b: paramètres du modèle
# - X, y: données
# - reg_weight_a: poids de la régularisation L2 sur les paramètres "a"
# - reg_weight_b: poids de la régularisation L2 sur le paramètre "b"
# return:
# - loss value
#
# Modification of a and b must inplace
def gradient_descent_step_L2(a, b, X, y, stepsize, reg_weight_a=0, reg_weight_b=0):
    assert reg_weight_a == 0  # asserts à supprimer quand vous aurez implémenté la régularisation!
    assert reg_weight_b == 0
    # TODO
    # ...

In [ ]:
# Gradient descent
def gradient_descent_L2(X, y, stepsize, num_epoch=20, reg_weight_a=0, reg_weight_b=0):
    a = np.zeros(X.shape[1])
    b = np.zeros(1)
    
    losses = list()
    timing = list()
    
    for _ in range(num_epoch):
        losses.append(gradient_descent_step_L2(a, b, X, y, stepsize, reg_weight_a=reg_weight_a, reg_weight_b=reg_weight_b))
    
    return a, b, losses


In [ ]:
a, b, losses = gradient_descent_L2(X_train, y_train, 0.1)

print("Erreur moyenne sur le test: ", mean_square_error(y_test, predict(a, b, X_test)))

# affiche la losse au fil des époques
plt.plot(range(len(losses)), losses)

Faites des expériences sur le modèle :

- qu'arrive-t-il quand on fait varier la régularisation? (sur a, sur b, les deux, que sur b, etc)
- qu'est ce qu'on observe quand on entraine directement sur les données de test plutôt que sur les données de train ? Impact de la régularisation dans ce cas ?

**Attention:** Il faut que je puisse refaire vos expériences, qui seront décrites et analysées dans le rapport, en lançant les cellules ci-dessous ! N'hésiter pas à laisser des commentaires dans les cellules pour que je puisse facilement faire le lien entre l'expérience et le commentaire dans le rapport. Vous pouvez évidemment ajouter des cellules.

De plus, laissez les graphes sur le notebook que je puisse les visualiser sans avoir à ré-executer le code ! (les graphes affichés sont sauvegardés dans la source du notebook).

# Descente de gradient et régularization L1

Pour cette partie, vous implémenterez 2 variantes de la régularization L1 :

- d'abord une implémentation standard, cas heuristic=False
- ensuite le cas heuristic=True : à chaque fois que vous faite une étape de gradient sur a, vous devez mettre à 0 toutes les coordonnées qui ont changées de signe après la mise à jour

**Attention:** dans cette partie, nous ne régularisons que le vecteur "a"

- Pour calculer le gradient de la loss L1, vous pouvez utiliser la fonction np.sign. Pourquoi ?
- La fonction copy de numpy pour aussi vous être utile ! Pourquoi ?

In [ ]:
# vous pouvez utiliser des booléens comme masque pour faire des mises à jour conditionnelles.
# Par exemple ici pour mettre toutes les valeurs positives à 0
a = np.random.rand(5) - 0.5
print(a)
mask = (a > 0)
print(mask)
a[mask] = 0
print(a)

In [ ]:
# arguments:
# - a, b: paramètres du modèle
# - X, y: données
# - reg_weight_a: poids de la régularisation L2 sur les paramètres "a"
# - heuristic: si vrai, appliquer l'heuristique pour forcer les poids à 0
# return:
# - loss value
#
# Modification of a and b must inplace
def gradient_descent_step_L1(a, b, X, y, stepsize, reg_weight_a=0, heuristic=False):
    assert reg_weight_a == 0  # asserts à supprimer quand vous aurez implémenté la régularisation!
    # TODO
    # ...

In [ ]:
# Gradient descent
def gradient_descent_L1(X, y, stepsize, num_epoch=20, reg_weight_a=0, heuristic=False):
    a = np.zeros(X.shape[1])
    b = np.zeros(1)
    
    losses = list()
    timing = list()
    
    for _ in range(num_epoch):
        losses.append(gradient_descent_step_L1(a, b, X, y, stepsize, reg_weight_a=reg_weight_a, heuristic=heuristic))
    
    return a, b, losses


In [ ]:
a, b, losses = gradient_descent_L1(X_train, y_train, 0.1, reg_weight_a=0.1, heuristic=False)

plt.plot(losses)

Faites quelques tests d'entrainement, avec et sans heuristique, et en faisant varier la régularization L1.

- qu'observez vous au niveau des résultats ?
- qu'observez vous au niveau du nombre paramètres égale à 0 dans le vecteur "a" ? Pour calculer cela vous pouvez utiliser np.isclose(a, 0).sum()
- **si vous avez le temps** comparer avec la régularisation L2

# Coordinate descent

Dans cette partie nous ne régulariserons pas b. Comme avant, commencez par implémenter sans régularisation, et ensuite implémentez la régularisation.

Qu'observez vous comparé à la descente de gradient ?

In [ ]:
# Effectue une étape de descente de coordonnée pour le vecteur de paramêtre "a"
# La mise à jour doit se faire inplace
# arguments
# - a, b: comme précédemment
# - X, y: données d'entrainement
# - coordinate: index dans le vecteur de paramêtres "a" à mettre à jour
# - reg_weight_a: le poids de la régularisation L2
# Pas de retour attendu
def coord_descent_a_L2(a, b, X, y, coordinate, reg_weight_a=0):
    assert reg_weight_a == 0 # à supprimé une fois la regularisation implémentée
    # TODO
    # ...

# Effectue une étape de descente de coordonnée pour le paramêtre "b"
# La mise à jour doit se faire inplace
# arguments
# - a, b: comme précédemment
# - X, y: données d'entrainement
# Pas de retour attendu
def coord_descent_b(a, b, X, y):
    # TODO
    # ...
    

# Effectue une étape complête de descente de coordonnées sur "a" et "b"
# (correspond à une epoch pour la descente de coordonées)
def coord_descent_step_L2(a, b, X, y, reg_weight_a=0):
    # TODO
    # ...


# Doit fonctionner comme gradient_descent_L2 mais pour la descente de coordonées
def coordinate_descent_L2(X, y, stepsize, num_epoch=20, reg_weight_a=0):
    a = np.zeros(X.shape[1])
    b = np.zeros(1)
    losses = list()
    
    for _ in range(num_epoch):
        r = X @ a + b - y
        losses.append(0.5 * (r ** 2).sum() / X.shape[0])
        coord_descent_step_L2(a, b, X, y, reg_weight_a=reg_weight_a)

    return a, b, losses



In [ ]:
a_gd, b_gd, losses_gd = gradient_descent_L2(X, y, stepsize=0.01, num_epoch=20)
a_cd, b_cd, losses_cd = coordinate_descent_L2(X, y, stepsize=0.01, num_epoch=20)

In [ ]:
plt.plot(losses_gd, color="blue")
plt.plot(losses_cd, color="red")

In [ ]:
plt.yscale("log")
plt.plot(losses_gd, color="blue")
plt.plot(losses_cd, color="red")

# Fast coordinate descent

**Pourcette partie, pas besoin de régularisation**

Dans la formule de mise à jour des coordonnées de "a", la version "naive" consiste à implémenter la formule tel quel.
Cependant, on peut observer qu'un terme du nominateur ressemble au vecteur suivant :
$$
r = y - (Xa + b)
$$
mais où le produit matricielle $Xa$ doit ignorer une colonne de X et un élément de a.
Par exemple, lorsque l'on met à jour l'élément $c$, le terme dans le nominateur devient :
$$
y - (Xa - X_{-, c} * a[c] + b)
$$
où $X_{-, c}$ correspond à la colonne c de X.

- Comment ce fait permet d'accélerer les calculs dans l'algorithme ? Expliquer.
- Implémenter cette variante dans la fonction ci dessous et tester.

In [ ]:
# Effectue une étape complète de descente de coordonnées sur "a" et "b"
# (correspond à une epoch pour la descente de coordonées, le tout en une seule fonction)
# Pas de retour attendu
def coord_descent_step_fast(a, b, X, y):
    coord_descent_b(a, b, X, y)
    # TODO
    # ...


# Doit fonctionner comme gradient_descent_L2 mais pour la descente de coordonées
def coordinate_descent_fast(X, y, stepsize, num_epoch=20):
    a = np.zeros(X.shape[1])
    b = np.zeros(1)
    losses = list()
    
    for _ in range(num_epoch):
        r = X @ a + b - y
        losses.append(0.5 * (r ** 2).sum() / X.shape[0])
        coord_descent_step_fast(a, b, X, y)

    return a, b, losses



In [ ]:
a_cd2, b_cd2, losses_cd2 = coordinate_descent_fast(X, y, stepsize=0.01, num_epoch=20)

In [ ]:
plt.plot(losses_cd2)